# Glow-TTS Training
Glow-TTS 학습 진행
음성의 말투와 음색을 결정하는 모델

## 1. 런타임에 할당된 GPU 확인

만약, `GPU: NVIDIA-SMI has failed because it couldn't communicate with the NVIDIA driver. Make sure that the latest NVIDIA driver is installed and running.` 라는 메시지가 출력된다면, 위쪽 메뉴에서 `런타임 -> 런타임 유형 변경`을 클릭하고 하드웨어 가속기를 `GPU`로 변경하여 저장한 후 다시 실행 필요

In [1]:
import os
GPU_NAME = os.popen('nvidia-smi --query-gpu=name --format=csv,noheader').read().strip()
os.environ['GPU_NAME'] = GPU_NAME
print(f'GPU: {GPU_NAME}')

GPU: Tesla T4


## 2. 구글 드라이브 마운트

마운트할 구글 드라이브 내에 다음 파일이 존재해야함

- `/Colab Notebooks/data/filelists.zip`

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


## 3. 필수 라이브러리 및 함수 불러오기


In [3]:
import sys
from pathlib import Path

In [4]:
%cd /content
!git clone --depth 1 https://github.com/sce-tts/TTS.git -b sce-tts
%cd /content/TTS
!python setup.py develop

/content
Cloning into 'TTS'...
remote: Enumerating objects: 447, done.
remote: Counting objects: 100% (447/447), done.
remote: Compressing objects: 100% (413/413), done.
remote: Total 447 (delta 56), reused 222 (delta 22), pack-reused 0
Receiving objects: 100% (447/447), 13.77 MiB | 17.84 MiB/s, done.
Resolving deltas: 100% (56/56), done.
/content/TTS
/content/TTS/setup.py:15: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if LooseVersion(sys.version) < LooseVersion("3.6") or LooseVersion(sys.version) > LooseVersion("3.9"):
Traceback (most recent call last):
  File "/content/TTS/setup.py", line 16, in <module>
    raise RuntimeError(
RuntimeError: TTS requires python >= 3.6 and <3.9 but your Python version is 3.10.11 (main, Apr  5 2023, 14:15:10) [GCC 9.4.0]


## 4. 학습할 데이터셋 불러오기

학습에 사용할 음성 데이터를 구글 드라이브에서 가져온다.

mimic recording studio로 생성한 `filelists.zip` 필요

In [5]:
%cd /content/TTS
!cp "/content/drive/My Drive/Colab Notebooks/data/filelists.zip" ./filelists.zip
!rm -rf ./filelists
!unzip -q filelists.zip -d ./filelists

/content/TTS


## 5. 사전 학습 데이터 불러오기


> 사전 학습 데이터가 구글 드라이브에 존재하지 않을 경우, 다른 사람의 사전 학습 데이터를 내려받음.



In [6]:
%cd /content/TTS
!mkdir -p "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2"
if not Path("/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/config.json").exists():
    !gdown --id 1DMKLdfZ_gzc_z0qDod6_G8fEXj0zCHvC -O glowtts-v2.zip
    !unzip -q glowtts-v2.zip -d ./
    !cp -R ./glowtts-v2/* "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/"

/content/TTS


In [7]:
%cd /content/TTS
if not Path("/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/scale_stats_new.npy").exists():
    !python TTS/bin/compute_statistics.py "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/config.json" "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/scale_stats_new.npy" --data_path "/content/TTS/filelists/wavs/"

/content/TTS


In [8]:
with open("/content/TTS/test_sentences.txt", mode="w") as f:
    f.write("""아래 문장들은 모델 학습을 위해 사용하지 않은 문장들입니다.
서울특별시 특허허가과 허가과장 허과장.
경찰청 철창살은 외철창살이고 검찰청 철창살은 쌍철창살이다.
지향을 지양으로 오기하는 일을 지양하는 언어 습관을 지향해야 한다.
그러니까 외계인이 우리 생각을 읽고 우리 생각을 우리가 다시 생각토록 해서 그 생각이 마치 우리가 생각한 것인 것처럼 속였다는 거냐?""")

## 6. TensorBoard 실행

학습 진행을 확인하기 위해 TensorBoard를 실행

설정 버튼을 눌러 auto reload를 설정해 30초마다 자동 갱신 가능

In [9]:
%load_ext tensorboard
%tensorboard --logdir="/content/drive/My Drive/Colab Notebooks/data/glowtts-v2"

<IPython.core.display.Javascript object>

## 7. Glow-TTS 학습 진행

학습이 정상적으로 진행되면, 이 셀은 종료되지 않고 계속 실행되는 상태를 유지한다.

이전에 학습을 진행하던 모델을 이어서 학습을 진행하시려면 다음과 같이 수정한 후 실행한다.

- 아래 셀에서 2 ~ 3번째 줄의 코드를 주석을 해제한다다
- 3번째 줄의 경로를 이어서 학습을 진행할 모델의 경로로 변경한다다.  
(예시: `/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/glowtts-v2-May-31-2021_08+17AM-d897f2e`)
- 4번째 줄 아래의 코드를 제거한다.


In [10]:
%cd /content/TTS
!(python TTS/bin/train_glow_tts.py \
    -continue_path "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/glowtts-v2-April-17-2022_04+46AM-3aa165a/checkpoint_32000.pth.tar")
!(python TTS/bin/train_glow_tts.py \
    --config_path "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/glowtts-v2-April-17-2022_04+46AM-3aa165a/config.json" \
    --coqpit.datasets.0.path "/content/TTS/filelists"  \
    --coqpit.audio.stats_path "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/scale_stats_new.npy"  \
    --coqpit.test_sentences_file "/content/TTS/test_sentences.txt"  \
    --coqpit.output_path "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/"  \
    --coqpit.num_loader_workers 2  \
    --coqpit.num_val_loader_workers 2  \
   --restore_path "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/model_file.pth.tar")

/content/TTS
Traceback (most recent call last):
  File "/content/TTS/TTS/bin/train_glow_tts.py", line 17, in <module>
    from TTS.tts.datasets.preprocess import load_meta_data
ModuleNotFoundError: No module named 'TTS'
Traceback (most recent call last):
  File "/content/TTS/TTS/bin/train_glow_tts.py", line 17, in <module>
    from TTS.tts.datasets.preprocess import load_meta_data
ModuleNotFoundError: No module named 'TTS'
